### Tokenizing + Vectorization

In [1]:
import string
import pandas as pd # pip install pandas
import nltk # pip install nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
from sklearn.feature_extraction.text import TfidfVectorizer # pip install scikit-learn
from sklearn import decomposition
import numpy as np # pip install numpy

In [2]:
pd.set_option('display.max_columns', None)  # or 1000
pd.set_option('display.max_rows', None)  # or 1000
pd.set_option('display.max_colwidth', None)  # or 199

df = pd.read_csv("../dataset/_compiled/Compiled.csv")

In [3]:
def remove_punctuation(cell):
    return cell.translate(str.maketrans('', '', string.punctuation))

def tokenizer(text):
    # 1-gram tokens of more than 3 characters
    word_tokens = [x for x in word_tokenize(text) if len(x) > 3]
    # remove stop words 
    filtered_tokens = [word for word in word_tokens if word not in set([remove_punctuation(x) for x in [*stopwords.words('english'), "im", "were", "youre", "thats", "theres"]])]
    # lemmatize the tokens 
    lemmatized_tokens = [lemmatizer.lemmatize(token) for token in filtered_tokens]
    return lemmatized_tokens

In [4]:
# https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfVectorizer.html
# vectorize to a matrix of TF-IDF features
# df = document frequency. 

tf_vectorizer = TfidfVectorizer(tokenizer=tokenizer,
                                max_df=0.75, max_features=10000, stop_words = "english",
                                use_idf=True, norm=None, token_pattern=None)
tf_vectors = tf_vectorizer.fit_transform(df["Translated"])  

/Users/ray/Documents/Obsidian/Arki's Vault/2_CS 132/_Code/scraper/.scrape/lib/python3.12/site-packages/sklearn/feature_extraction/text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['le'] not in stop_words.
  warnings.warn(


In [5]:
# https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.LatentDirichletAllocation.html

n_topics = 10
lda = decomposition.LatentDirichletAllocation(n_components=n_topics, max_iter=30, 
                                              learning_method='online', learning_offset=60, n_jobs=1, random_state=42)
W = lda.fit_transform(tf_vectors)
H = lda.components_

In [6]:
# Show top 15 relevant words for each of the 25 topics
num_words = 10
vocab = np.array(tf_vectorizer.get_feature_names_out())
top_words = lambda t: [vocab[i] for i in np.argsort(t)[:-num_words-1:-1]]
topic_words = ([top_words(t) for t in H])
topics = [', '.join(t) for t in topic_words]
df_topics = pd.DataFrame(topics, columns=['Keywords'])
df_topics['Topic ID'] = range(1, len(topics) + 1)
df_topics

Keywords  \
0          employee, philippine, sagility, cial, market, department, australian, worker, stock, aspect   
1                      information, technology, work, company, like, bos, want, time, project, manager   
2       information, technology, month, resignation, day, immediately, hospital, render, leave, resign   
3  post, applicant, recruiter, reference, technology, comment, information, reddit, quitting, multiple   
4                interview, information, technology, company, said, offer, human, resource, time, hour   
5               work, party, company, people, christmas, technology, information, friend, really, like   
6     salary, philippine, information, technology, experience, increase, year, company, position, know   
7          said, employee, vacation, information, labor, payment, terminated, technology, school, work   
8                 vacation, food, hour, leaf, worklife, balance, work, information, technology, people   
9  organization, mainte, monthly, health, comptia, professor, program, course, information, technology   

   Topic ID  
0         1  
1         2  
2         3  
3         4  
4         5  
5         6  
6         7  
7         8  
8         9  
9        10

In [7]:
# Assign topic to each tweet
topicid = ["Topic " + str(i+1) for i in range(lda.n_components)]
tweetid = ["Submission " + str(i+1) for i in range(len(df["Translated"]))]

df_topics_lda = pd.DataFrame(np.round(W,2), columns=topicid, index=tweetid)
significanttopic = np.argmax(df_topics_lda.values, axis=1)+1

df_topics_lda['dominant_topic'] = significanttopic
df_topics_lda['breakdown'] = df_topics_lda.apply(lambda row: '\n'.join([f'{col}: {row[col]}' 
                                                        for col in sorted(df_topics_lda.columns, key=lambda x: row[x], reverse=True) 
                                                        if row[col] > 0 and col != 'dominant_topic']), axis=1)
df_topics_lda.head(10)

Topic 1  Topic 2  Topic 3  Topic 4  Topic 5  Topic 6  Topic 7  \
Submission 1      0.00     0.54     0.00     0.00     0.00     0.00     0.00   
Submission 2      0.00     0.25     0.00     0.00     0.00     0.00     0.00   
Submission 3      0.00     0.00     0.05     0.19     0.39     0.06     0.00   
Submission 4      0.00     0.00     0.00     0.00     0.70     0.00     0.15   
Submission 5      0.00     0.92     0.07     0.00     0.00     0.00     0.00   
Submission 6      0.00     0.10     0.18     0.00     0.11     0.00     0.00   
Submission 7      0.00     0.35     0.00     0.00     0.10     0.03     0.00   
Submission 8      0.00     0.37     0.00     0.62     0.00     0.00     0.00   
Submission 9      0.88     0.00     0.10     0.00     0.00     0.00     0.00   
Submission 10     0.00     0.75     0.25     0.00     0.00     0.00     0.00   

               Topic 8  Topic 9  Topic 10  dominant_topic  \
Submission 1      0.45     0.00      0.00               2   
Submission 2      0.75     0.00      0.00               8   
Submission 3      0.30     0.00      0.00               5   
Submission 4      0.00     0.15      0.00               5   
Submission 5      0.00     0.00      0.00               2   
Submission 6      0.00     0.00      0.62              10   
Submission 7      0.52     0.00      0.00               8   
Submission 8      0.00     0.00      0.00               4   
Submission 9      0.00     0.00      0.00               1   
Submission 10     0.00     0.00      0.00               2   

                                                                              breakdown  
Submission 1                                               Topic 2: 0.54\nTopic 8: 0.45  
Submission 2                                               Topic 8: 0.75\nTopic 2: 0.25  
Submission 3   Topic 5: 0.39\nTopic 8: 0.3\nTopic 4: 0.19\nTopic 6: 0.06\nTopic 3: 0.05  
Submission 4                                 Topic 5: 0.7\nTopic 7: 0.15\nTopic 9: 0.15  
Submission 5                                               Topic 2: 0.92\nTopic 3: 0.07  
Submission 6                 Topic 10: 0.62\nTopic 3: 0.18\nTopic 5: 0.11\nTopic 2: 0.1  
Submission 7                  Topic 8: 0.52\nTopic 2: 0.35\nTopic 5: 0.1\nTopic 6: 0.03  
Submission 8                                               Topic 4: 0.62\nTopic 2: 0.37  
Submission 9                                                Topic 1: 0.88\nTopic 3: 0.1  
Submission 10                                              Topic 2: 0.75\nTopic 3: 0.25

In [8]:
# Visualize topics
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
import plotly.express as px # pip install plotly

# Apply t-SNE for dimensionality reduction
tsne = TSNE(n_components=2, random_state=42)
tsne_result = tsne.fit_transform(df_topics_lda.iloc[:,:10])

# Apply K-means clustering
n_topics = 10
kmeans = KMeans(n_clusters=n_topics, n_init=10, random_state=42)
cluster_labels = kmeans.fit_predict(df_topics_lda.iloc[:,:10])

In [9]:
# Create a new dataframe with t-SNE coordinates and cluster labels
import textwrap

def split_text(text, max_length):
  lines = textwrap.wrap(text, width=max_length, break_long_words=False)
  return "<br>".join(lines)

df_topics_cluster = pd.DataFrame({'X': tsne_result[:, 0],
                                  'Y': tsne_result[:, 1],
                                  'Submission': df["Translated"],
                                  'Cluster': df_topics_lda.reset_index()['dominant_topic'].astype(str), # topics via LDA
                                  # 'Cluster': cluster_labels},                                         # clusters via K-means
                                  'Breakdown': df_topics_lda.reset_index()['breakdown']})

df_topics_cluster['Submission'] = df_topics_cluster['Submission'].apply(lambda x: split_text(x, 40))
df_topics_cluster['Breakdown'] = df_topics_cluster['Breakdown'].str.replace('\n','<br>')

df_topics_cluster.head(10)

X          Y  \
0 -16.487108  18.768225   
1 -22.146912  24.107485   
2 -22.046141  -4.459234   
3 -12.231421 -11.624436   
4  30.410311  -1.973994   
5  -1.329584   5.244882   
6 -19.263718  19.851551   
7  -3.591256 -43.286163   
8  39.851849 -24.674173   
9  16.375126  -4.173429   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 Submission  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [10]:
# Plot submissions as colored points
df_topics_cluster.sort_values('Cluster', key=lambda x: pd.to_numeric(x, errors='coerce'), inplace=True)

fig = px.scatter(df_topics_cluster, x='X', y='Y', color='Cluster', 
                 title='Topic Clustering using LDA and t-SNE',
                 hover_name='Submission',
                 hover_data={'X':False, 'Y':False, 'Cluster':False, 'Submission':False, 'Breakdown':True})

for i, keyword in enumerate(df_topics['Keywords']):
  fig.add_annotation(
    x=0,
    y=-0.2*(i/5)-0.08,
    text="Topic %d: %s"%(i+1, keyword.replace(' ', ', ')),
    showarrow=False,
    xref='paper',
    yref='paper',
    align='left',
    font=dict(color=fig.data[i].marker['color'])
  )

fig.update_layout(height=710,
                  xaxis_title='', yaxis_title='',
                  margin=dict(b=200),
                  paper_bgcolor='#2c3e50',
                  title=dict(font=dict(color='white')),
                  legend=dict(title="Topic", font=dict(color='white')))
# !pip install nbformat
# restart kernel
fig.show()